# Autoencoders
## Inteligencia Computacional 2021-2, Grupo 8a
Nicolás Canales, Matías Vergara

Este notebook tiene por objetivo aplicar Autoencoders sobre las curvas de luz con características computadas y visualizar el código resultante en búsqueda de clusters. Para ello se utilizará un cuello de botella bidimensional.


Recordemos que los objetos con los que estamos trabajando son aquellos de tipo periódico, clasificados por ALeRCE como: "LPV", "Periodic-Other", "RRL", "CEP", "E" o "DSCT". 

A lo largo del notebook se irá variando la arquitectura a usar, así como la cantidad de features de entrada y el tratamiento del desbalance de los datos. 

### Referencias:
Adnan Karol, Introduction to 2 dimensional LSTM autoencoder - https://medium.com/analytics-vidhya/introduction-to-2-dimensional-lstm-autoencoder-47c238fd827f

B. Zong et al. “Deep Autoencoding Gaussian Mixture Model for Unsupervised Anomaly Detection”. ICLR 2018 

Jason Brownlee, A Gentle Introduction to LSTM Autoencoders - https://machinelearningmastery.com/lstm-autoencoders/

### Librerías

In [ ]:
import pandas as pd
import numpy as np

from tensorflow import keras
from tensorflow.python.keras.layers import Input, Dense,RepeatVector, TimeDistributed, Dense, Dropout, LSTM
from tensorflow.python.keras.models import Sequential
from tensorflow.keras.layers import Input, Add, Dense, Activation, ZeroPadding2D, BatchNormalization, Flatten, Conv2D, AveragePooling2D, MaxPooling2D, Dropout
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.initializers import glorot_uniform
from tensorflow.keras.optimizers import SGD

import matplotlib.pyplot as plt
%matplotlib inline

import sklearn
from sklearn.preprocessing import StandardScaler, QuantileTransformer, RobustScaler
from sklearn.model_selection import train_test_split
from sklearn.cluster import KMeans

from tensorflow.keras.callbacks import EarlyStopping


from io import BytesIO
from PIL import Image
import base64
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import HoverTool, ColumnDataSource, CategoricalColorMapper
from bokeh.palettes import Spectral10, Spectral6

output_notebook()
early_stopping = EarlyStopping(monitor='loss', patience=4, verbose=0,
    mode='auto', baseline=None, restore_best_weights=False)


### Traer la data

In [ ]:
# !gdown --id 1HFEbip5SX591MCLi-S6DKw7LEx-CJFNt # data aumentada con las sinteticas originales
# !gdown --id 1WNhzNbJF44Z2upm1XEwZE_gAWM3M2s9A # data aumentada con las sinteticas nuevas
!gdown --id 1qY3HYGq7rH5ZzwM_vgshAK9lHQIzXsTf # data aumentada con las sinteticas nuevas x 10
# !gdown --id 1XCl8BiVOP7aheBYjOHIAM378s_34-8kl #reduced_data, misma data pero subsampleando las clases
                                              #sobrerepresentadas        

Downloading...
From: https://drive.google.com/uc?id=1qY3HYGq7rH5ZzwM_vgshAK9lHQIzXsTf
To: /content/augmented_features (2).csv
100% 169M/169M [00:00<00:00, 169MB/s]


In [ ]:
data = pd.read_csv("augmented_features.csv", index_col=0)

FileNotFoundError: ignored

In [ ]:
data.head()

Estandarizamos las features (tienen escalas muy distintas):

In [ ]:
scaler = QuantileTransformer() #StandardScaler o QuantileTransformer
data_scaled = scaler.fit_transform(data.drop(labels="target", axis=1))

### Funcion para plotear

In [ ]:
def show_scatter(pred, use_color = True):
  data_df = pd.DataFrame(pred, columns=('x', 'y'))
  data_df['target'] = [x for x in data.target]

  datasource = ColumnDataSource(data_df)
  if use_color:
    color_mapping = CategoricalColorMapper(factors=["E", "RRL", "CEP", "DSCT", "LPV", "Periodic-Other"],
                                        palette=Spectral6)

  plot_figure = figure(
      title='Autoencoder projection of the periodic light curves',
      plot_width=1200,
      plot_height=600,
      tools=('pan, wheel_zoom, reset')
  )

  if use_color:
    plot_figure.cross(
        'x',
        'y',
        source=datasource,
        color=dict(field='target', transform=color_mapping),
        line_alpha=0.5,
        fill_alpha=0,
        size=4,
        legend='target'
    )
  else:
        plot_figure.cross(
        'x',
        'y',
        source=datasource,
        line_alpha=0.5,
        fill_alpha=0,
        size=4,
        legend='target'
    )
  show(plot_figure)

### Crear el modelo de autoencoder


In [ ]:
encoding_dim = 9
input_df = Input(shape=(98,))


# Glorot normal initializer (Xavier normal initializer) draws samples from a truncated normal distribution 

x = Dense(encoding_dim, activation='relu')(input_df)
x = Dense(120, activation='relu', kernel_initializer = 'glorot_uniform')(x)
x = Dense(120, activation='relu', kernel_initializer = 'glorot_uniform')(x)
x = Dense(90, activation='relu', kernel_initializer = 'glorot_uniform')(x)

encoded = Dense(2, activation='relu', kernel_initializer = 'glorot_uniform')(x)

x = Dense(90, activation='relu', kernel_initializer = 'glorot_uniform')(encoded)
x = Dense(160, activation='relu', kernel_initializer = 'glorot_uniform')(x)

decoded = Dense(98, kernel_initializer = 'glorot_uniform')(x)

# autoencoder
autoencoder = Model(input_df, decoded)

#encoder - used for our dimention reduction
encoder = Model(input_df, encoded)

autoencoder.compile(optimizer= 'adam', loss='mean_squared_error')

### Experimentando con todas las features, data completa

In [ ]:
autoencoder.fit(data_scaled, data_scaled, batch_size = 64, epochs = 120,  verbose = 1, callbacks=[early_stopping])

In [ ]:
pred = encoder.predict(data_scaled)

In [ ]:
show_scatter(pred)

### Y si probamos con algunas features en lugar de todas?
Análogo a lo que hicimos con UMAP, veremos si el resultado del encoder mejora al considerar solo ciertas features, en lugar de todas las disponibles. 

In [ ]:
interest_features = [
                     'Multiband_period',
                     #'Period_band_g',
                     #'Period_band_r',
                     #'GP_DRW_sigma_r', 
                     #'GP_DRW_tau_g',
                     #'GP_DRW_sigma_r',
                     #'GP_DRW_tau_r',
                     #'Harmonics_mag_1_g',
                     #'Harmonics_mag_1_r',
                     #'Harmonics_mse_r', # comentar esta da otro conjunto viable
                     #'Harmonics_mse_g', ##
                     #'Power_rate_1/4', ##
                     #'Power_rate_1/3', ##
                     #'Power_rate_1/2', ##
                     #'Power_rate_2', ##
                     #'Power_rate_3', ##
                     #'Power_rate_4', ##
                     #'AndersonDarling_g', ##
                     #'AndersonDarling_r', ##
                     #'Autocor_length_g',
                     #'Autocor_length_r',
                     #'IAR_phi_g',
                     #'IAR_phi_r',
                     #'Skew_g',
                     #'Skew_r',
                     #'StetsonK_r',
                     #'StetsonK_g',
                     #'iqr_g',
                     #'iqr_r',
                     #'Amplitude_g',
                     'Mean_g',
                     #'Meanvariance_g',
                     #'Amplitude_r',
                     'Mean_r',
                     #'Meanvariance_r',
                     #'PairSlopeTrend_r',
                     'target'
                     #'LinearTrend_r',
                     #'ExcessVar_r',
                     #'LinearTrend_g',
                     #'ExcessVar_g',
                     #'PPE',
                     #'Psi_CS_g',
                     #'Psi_CS_r',
                     #'Psi_eta_g',
                     #'Psi_eta_r',
                     #'iqr_g',
                     #'iqr_r',                    
]

data = data[interest_features]
data.shape

Actualizamos nuestra variable data_scaled para que ahora se calcule en base a las columnas de interés solamente

In [ ]:
scaler = QuantileTransformer()
data_scaled = scaler.fit_transform(data.drop(labels="target", axis=1))

In [ ]:
# This is the dimension of the original space
input_dim = 3
# This is the dimension of the latent space (encoding space)
latent_dim = 2

encoder = Sequential([
    Dense(120, activation='relu', kernel_initializer = 'glorot_uniform', input_shape=(input_dim,)),
    Dense(120, activation='relu', kernel_initializer = 'glorot_uniform'),
    Dense(90, activation='relu', kernel_initializer = 'glorot_uniform'),
    Dense(latent_dim, activation='relu')
])

decoder = Sequential([
    Dense(90, activation='relu', input_shape=(latent_dim,), kernel_initializer = 'glorot_uniform'), 
    Dense(128, activation='relu', kernel_initializer = 'glorot_uniform'),
    Dense(256, activation='relu', kernel_initializer = 'glorot_uniform'),
    Dense(input_dim, activation=None)
])

autoencoder = keras.models.Sequential([encoder, decoder])
autoencoder.compile(loss='mse', optimizer='adam')

In [ ]:
history = autoencoder.fit(data_scaled, data_scaled, epochs=50, batch_size=64,verbose=1, callbacks=[early_stopping])

In [ ]:
pred = encoder.predict(data_scaled)

In [ ]:
show_scatter(pred)

###Y si probamos con los datos subsampleados?


In [ ]:
!gdown --id 1XCl8BiVOP7aheBYjOHIAM378s_34-8kl #reduced_data, misma data pero subsampleando las clases
                                              #sobrerepresentadas


In [ ]:
data = pd.read_csv("reduced_data.csv", index_col=0)

In [ ]:
interest_features = [
                     'Multiband_period',
                     'Period_band_g',
                     'Period_band_r',
                     'GP_DRW_sigma_r', 
                     'GP_DRW_tau_g',
                     'GP_DRW_sigma_r',
                     'GP_DRW_tau_r',
                     'Harmonics_mag_1_g',
                     'Harmonics_mag_1_r',
                     'Harmonics_mse_r', # comentar esta da otro conjunto viable
                     'Harmonics_mse_g', ##
                     'Power_rate_1/4', ##
                     'Power_rate_1/3', ##
                     'Power_rate_1/2', ##
                     'Power_rate_2', ##
                     'Power_rate_3', ##
                     'Power_rate_4', ##
                     'AndersonDarling_g', ##
                     'AndersonDarling_r', ##
                     'Autocor_length_g',
                     'Autocor_length_r',
                     'target'
                     
]

data = data[interest_features]
data.head()
data.shape

In [ ]:
scaler = QuantileTransformer()
data_scaled = scaler.fit_transform(data.drop(labels="target", axis=1))

In [ ]:
# This is the dimension of the original space
input_dim = 21
# This is the dimension of the latent space (encoding space)
latent_dim = 2

encoder = Sequential([
    Dense(2048, activation='relu', kernel_initializer = 'glorot_uniform', input_shape=(input_dim,)),
    Dense(1024, activation='relu', kernel_initializer = 'glorot_uniform'),
    Dense(512, activation='relu', kernel_initializer = 'glorot_uniform'),
    Dense(256, activation='selu', kernel_initializer = 'glorot_uniform'),
    Dense(latent_dim, activation='sigmoid')
])

decoder = Sequential([
    Dense(512, activation='relu', input_shape=(latent_dim,), kernel_initializer = 'glorot_uniform'), 
    Dense(1024, activation='relu', kernel_initializer = 'glorot_uniform'),
    Dense(2048, activation='relu', kernel_initializer = 'glorot_uniform'),
    Dense(input_dim, activation=None)
])
autoencoder = keras.models.Sequential([encoder, decoder])
autoencoder.compile(loss='mse', optimizer='adam')
history = autoencoder.fit(data_scaled, data_scaled, epochs=50, batch_size=64,verbose=1, callbacks=[early_stopping])

In [ ]:
pred = encoder.predict(data_scaled)

Usaremos distintas celdas para plottear los distintos intentos, para no perderlos e ir comparando.

In [ ]:
show_scatter(pred)

### Probemos la mejor configuración obtenida


Veamos si la configuración que mejor resultados dió para la data subsampleada funciona también con la data completa.

In [ ]:
data = pd.read_csv("augmented_features.csv", index_col=0)

interest_features = [
                     'Multiband_period',
                     'Mean_g',
                     'Mean_r',
                     'delta_period_g',
                     'delta_period_r',
                     'GP_DRW_sigma_r',
                     'GP_DRW_tau_g',
                     'GP_DRW_sigma_r',
                     'GP_DRW_tau_r',
                     'Harmonics_mag_1_g',
                     'Harmonics_mag_1_r',
                     'Harmonics_mse_r', 
                     'Harmonics_mse_g', 
                     'Power_rate_1/4', 
                     'AndersonDarling_g', 
                     'AndersonDarling_r', 
                     'iqr_g',
                     'iqr_r',
                     'Amplitude_g',
                     'Meanvariance_g',
                     'Amplitude_r',
                     'Meanvariance_r',
                     'PairSlopeTrend_g',
                     'PairSlopeTrend_r',
                     'target',
                     'LinearTrend_r',
                     'ExcessVar_r',
                     'LinearTrend_g',
                     'ExcessVar_g'
]


#data = data[interest_features]
scaler = QuantileTransformer()
data_scaled = scaler.fit_transform(data.drop(labels="target", axis=1))

In [ ]:
# This is the dimension of the original space
input_dim = 98
# This is the dimension of the latent space (encoding space)
latent_dim = 2

encoder = Sequential([
    Dense(50, activation='relu', kernel_initializer = 'glorot_uniform', input_shape=(input_dim,)),
    Dense(20, activation='relu', kernel_initializer = 'glorot_uniform'),
    Dense(latent_dim, activation='sigmoid')
])

decoder = Sequential([
    Dense(20, activation='relu', kernel_initializer = 'glorot_uniform', input_shape=(latent_dim,)), 
    Dense(50, activation='relu', kernel_initializer = 'glorot_uniform'),
    Dense(input_dim, activation=None)
])
autoencoder = keras.models.Sequential([encoder, decoder])
autoencoder.compile(loss='mse', optimizer='adam')
history = autoencoder.fit(data_scaled, data_scaled, epochs=50, batch_size=64,verbose=1, callbacks=[early_stopping])

Epoch 1/50
1510/1510 [==============================] - 6s 3ms/step - loss: 0.0627
Epoch 2/50
1510/1510 [==============================] - 5s 3ms/step - loss: 0.0529
Epoch 3/50
1510/1510 [==============================] - 5s 3ms/step - loss: 0.0519
Epoch 4/50
1510/1510 [==============================] - 5s 3ms/step - loss: 0.0514
Epoch 5/50
1510/1510 [==============================] - 5s 3ms/step - loss: 0.0510
Epoch 6/50
1510/1510 [==============================] - 5s 3ms/step - loss: 0.0506
Epoch 7/50
1510/1510 [==============================] - 5s 3ms/step - loss: 0.0503
Epoch 8/50
1510/1510 [==============================] - 5s 3ms/step - loss: 0.0501
Epoch 9/50
1510/1510 [==============================] - 5s 3ms/step - loss: 0.0500
Epoch 10/50
1510/1510 [==============================] - 5s 3ms/step - loss: 0.0496
Epoch 11/50
1510/1510 [==============================] - 5s 3ms/step - loss: 0.0494
Epoch 12/50
1510/1510 [==============================] - 5s 3ms/step - loss: 0.0491
E

In [ ]:
pred = encoder.predict(data_scaled)

In [ ]:
show_scatter(pred)
# plotly

In [ ]:
show_scatter(pred, use_color = False)

In [ ]:
data_df = pd.DataFrame(pred, columns=('x', 'y'))
data_df['target'] = [x for x in data.target]
data_df['oid'] = [x for x in data.index]
data_df.set_index('oid', inplace=True)
data_df.head()
data_df.to_csv("autoencoder_i.csv")
#apretado

**mezcla de gaussianas en el autoencoder**

graficar las curvas de luz de ciertos clusters pra ver como se parecen entre sí 
(hacer un estudio del cluster)

clusters con métricas



si nos queda tiempo, subclusters 


## Exploración 3D


In [ ]:
!gdown --id 1WNhzNbJF44Z2upm1XEwZE_gAWM3M2s9A # data aumentada con las sinteticas nuevas
# !gdown --id 1qY3HYGq7rH5ZzwM_vgshAK9lHQIzXsTf # data aumentada con las sinteticas nuevas x 10
# !gdown --id 1XCl8BiVOP7aheBYjOHIAM378s_34-8kl #reduced_data, misma data pero subsampleando las clases
                                              #sobrerepresentadas        

Downloading...
From: https://drive.google.com/uc?id=1WNhzNbJF44Z2upm1XEwZE_gAWM3M2s9A
To: /content/augmented_features.csv
100% 132M/132M [00:00<00:00, 197MB/s]


In [ ]:
data = pd.read_csv("augmented_features.csv", index_col=0)

interest_features = [
                     'Multiband_period',
                     'Mean_g',
                     'Mean_r',
                     'target'
]


data = data[interest_features]
#data.head()
scaler = QuantileTransformer()
data_scaled = scaler.fit_transform(data.drop(labels="target", axis=1))

In [ ]:
# This is the dimension of the original space
input_dim = 3
# This is the dimension of the latent space (encoding space)
latent_dim = 3

encoder = Sequential([
    Dense(133, activation='relu', kernel_initializer = 'glorot_uniform', input_shape=(input_dim,)),
    Dense(latent_dim, activation='sigmoid')
])

decoder = Sequential([
    Dense(133, activation='selu', kernel_initializer = 'glorot_uniform', input_shape=(latent_dim,)), 
    Dense(15, activation='relu', kernel_initializer = 'glorot_uniform'), 
    Dense(input_dim, activation=None)
])
autoencoder = keras.models.Sequential([encoder, decoder])
autoencoder.compile(loss='mse', optimizer='adam')
history = autoencoder.fit(data_scaled, data_scaled, epochs=50, batch_size=64,verbose=1, callbacks=[early_stopping])

Epoch 1/50
1205/1205 [==============================] - 3s 2ms/step - loss: 0.0129
Epoch 2/50
1205/1205 [==============================] - 3s 2ms/step - loss: 7.7384e-05
Epoch 3/50
1205/1205 [==============================] - 3s 2ms/step - loss: 3.3325e-05
Epoch 4/50
1205/1205 [==============================] - 3s 2ms/step - loss: 1.9178e-05
Epoch 5/50
1205/1205 [==============================] - 3s 2ms/step - loss: 1.5742e-05
Epoch 6/50
1205/1205 [==============================] - 3s 2ms/step - loss: 1.4456e-05
Epoch 7/50
1205/1205 [==============================] - 3s 2ms/step - loss: 1.3197e-05
Epoch 8/50
1205/1205 [==============================] - 3s 2ms/step - loss: 1.0373e-05
Epoch 9/50
1205/1205 [==============================] - 3s 2ms/step - loss: 9.8222e-06
Epoch 10/50
1205/1205 [==============================] - 3s 2ms/step - loss: 8.9122e-06
Epoch 11/50
1205/1205 [==============================] - 3s 2ms/step - loss: 1.0148e-05
Epoch 12/50
1205/1205 [======================

In [ ]:
pred = encoder.predict(data_scaled)

In [ ]:
pred = np.matrix(pred)

In [ ]:
# Celda para el caso 3D
pred = pd.DataFrame(pred, columns=('x', 'y', 'z')) 
pred['target'] = [x for x in data.target]
pred

x         y         z          target
0      0.469713  0.398531  0.332648               E
1      0.572077  0.609740  0.509167             RRL
2      0.414325  0.658205  0.298661             RRL
3      0.620358  0.670201  0.481478             RRL
4      0.581826  0.648724  0.507627               E
...         ...       ...       ...             ...
77076  0.514514  0.695906  0.452521  Periodic-Other
77077  0.341752  0.317505  0.273121  Periodic-Other
77078  0.344006  0.744946  0.289805  Periodic-Other
77079  0.252311  0.330496  0.184824  Periodic-Other
77080  0.381477  0.316989  0.359854  Periodic-Other

[77081 rows x 4 columns]

In [ ]:
# Celda para el caso 3D
import plotly.express as px
df = pred
fig = px.scatter_3d(df, x='x', y='y', z='z',
              color='target', opacity=0.3)
fig.show()